In [1]:
!sudo -H pip install -q transformers --upgrade

In [2]:
!sudo -H pip install https://github.com/casper-hansen/AutoAWQ/releases/download/v0.1.7/autoawq-0.1.7+cu118-cp38-cp38-linux_x86_64.whl

     |████████████████████████████████| 20.0MB 6.3MB/s eta 0:00:01
     |████████████████████████████████| 184kB 13.5MB/s eta 0:00:01
     |████████████████████████████████| 163kB 16.7MB/s eta 0:00:01
     |████████████████████████████████| 235kB 21.5MB/s eta 0:00:01
     |████████████████████████████████| 81kB 3.8MB/s eta 0:00:011


     |████████████████████████████████| 71kB 15.0MB/s eta 0:00:01
     |████████████████████████████████| 10.1MB 19.3MB/s eta 0:00:01
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 235kB 92.5MB/s eta 0:00:01
     |████████████████████████████████| 389kB 99.6MB/s eta 0:00:01
     |████████████████████████████████| 225kB 94.0MB/s eta 0:00:01
     |████████████████████████████████| 112kB 105.5MB/s eta 0:00:01
     |████████████████████████████████| 3.8MB 112.9MB/s eta 0:00:01
     |████████████████████████████████| 204kB 110.7MB/s eta 0:00:01


     |████████████████████████████████| 389kB 86.2MB/s eta 0:00:01
     |████████████████████████████████| 81kB 42.0MB/s  eta 0:00:01
     |████████████████████████████████| 1.5MB 109.2MB/s eta 0:00:01
     |████████████████████████████████| 471kB 101.1MB/s eta 0:00:01
     |████████████████████████████████| 2.1MB 113.4MB/s eta 0:00:01
     |████████████████████████████████| 81kB 43.1MB/s  eta 0:00:01
     |████████████████████████████████| 61kB 31.4MB/s eta 0:00:01
  Created wheel for pycountry: filename=pycountry-22.3.5-cp38-none-any.whl size=10681832 sha256=31c795ff282912028c658ab11615913da3ff7ecb1f49a7422f9148ab6274d8e3
  Stored in directory: /root/.cache/pip/wheels/7a/c3/f8/3e164430062ee08d5b8bc8fcd1b891ce54c7ad99871aa3adc1
Successfully built pycountry
  Created wheel for rouge-score: filename=rouge_score-0.1.2-cp38-none-any.whl size=24937 sha256=473f688247cc37fd821a2094d69f7249fd6a74add80c0564bbae8ad2bf5946c0
  Stored in directory: /root/.cache/pip/wheels/df/aa/59/74f33db3bbedf32

  Found existing installation: platformdirs 3.6.0
    Uninstalling platformdirs-3.6.0:
      Successfully uninstalled platformdirs-3.6.0
  Found existing installation: pluggy 1.0.0
    Uninstalling pluggy-1.0.0:
      Successfully uninstalled pluggy-1.0.0


In [1]:
import pandas

In [2]:
import numpy

In [3]:
from awq import AutoAWQForCausalLM
from transformers import AutoTokenizer

In [1]:
!pip list | grep cuda

nvidia-cuda-cupti-cu11   11.7.101  
nvidia-cuda-nvrtc-cu11   11.7.99   
nvidia-cuda-runtime-cu11 11.7.99   


In [2]:
import pandas

In [4]:
import torch
torch.__version__

'2.0.1+cu117'

In [5]:
model_path = '/data/quantization-trials/merged-model'

In [6]:
quant_path = '/data/quantization-trials/quant-model'

In [7]:
quant_config = {"zero_point":True,
               "q_group_size": 512,
               "w_bit": 4,
               "version": "GEMM"
               }

In [8]:
#load model
# model = AutoAWQForCausalLM.from_pretrained(model_path, **{"low_cpu_mem_usage":True})
model = AutoAWQForCausalLM.from_pretrained(model_path, safetensors=True, device_map='auto')

In [9]:
tokenizer = AutoTokenizer.from_pretrained(model_path, trust_remote_code=True)

In [10]:
#Quantize

model.quantize(tokenizer, quant_config=quant_config)

Repo card metadata block was not found. Setting CardData to empty.


Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Generating validation split: 0 examples [00:00, ? examples/s]

AWQ: 100%|██████████| 24/24 [06:42<00:00, 16.76s/it]


In [13]:
model.save_quantized(quant_path)
tokenizer.save_pretrained(quant_path)

('/data/quantization-trials/quant-model/tokenizer_config.json',
 '/data/quantization-trials/quant-model/special_tokens_map.json',
 '/data/quantization-trials/quant-model/vocab.json',
 '/data/quantization-trials/quant-model/merges.txt',
 '/data/quantization-trials/quant-model/added_tokens.json',
 '/data/quantization-trials/quant-model/tokenizer.json')

### Inference on quantized model

In [ ]:
from transformers import AutoModelForCausalLM, AutoTokenizer

model_id = quant_path
model = AutoModelForCausalLM.from_pretrained(model_id, device_map="cuda:0")

In [ ]:
!sudo -H pip install vllm

     |████████████████████████████████| 9.7MB 6.5MB/s eta 0:00:01
     |████████████████████████████████| 62.6MB 110kB/s  eta 0:00:01
     |████████████████████████████████| 211.8MB 31kB/s /s eta 0:00:01
     |████████████████████████████████| 102kB 46.3MB/s eta 0:00:01
     |████████████████████████████████| 61kB 31.6MB/s eta 0:00:01
     |███████████████▏                | 316.6MB 144.7MB/s eta 0:00:03

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



     |███████████████████████▌        | 492.4MB 140.0MB/s eta 0:00:02

     |███████████████████████▉        | 499.5MB 140.0MB/s eta 0:00:02

     |████████████████████████▏       | 506.6MB 140.0MB/s eta 0:00:02

...

     |████████████████████████████▏   | 644.8MB 150.8MB/s eta 0:00:01

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



     |████████████████████████████████| 731.7MB 7.0kB/s 
     |████████████████████████████████| 56.5MB 123kB/s  eta 0:00:01
     |████████████████████████████████| 102kB 45.9MB/s eta 0:00:01
     |███████████████████████         | 294.4MB 148.5MB/s eta 0:00:01

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



     |████████████████████████████████| 410.6MB 10kB/s 
     |████████████████████████████████| 829kB 71kB/s s eta 0:00:01
     |████████████████████████████████| 20.6MB 48kB/s s eta 0:00:01
  Created wheel for quantile-python: filename=quantile_python-1.1-cp38-none-any.whl size=3446 sha256=74e94f8162b55c5faf3dc251a25840707a9be2a66405001179a39852a8290382
  Stored in directory: /root/.cache/pip/wheels/9b/8f/31/06e34b94058c375cca1394c8b4109f3a1dd5243ed1cb856a2c
Successfully built quantile-python
ERROR: torchvision 0.15.2 has requirement torch==2.0.1, but you'll have torch 2.1.1 which is incompatible.
ERROR: torchaudio 2.0.2 has requirement torch==2.0.1, but you'll have torch 2.1.1 which is incompatible.
ERROR: xformers 0.0.22.post7 has requirement torch==2.1.0, but you'll have torch 2.1.1 which is incompatible.
  Found existing installation: triton 2.0.0
    Uninstalling triton-2.0.0:
      Successfully uninstalled triton-2.0.0
  Found existing installation: typing-extensions 4.1.1
    U

In [14]:
### Inference on quantized model, using vllm

from vllm import LLM, SamplingParams


# Create a sampling params object.
sampling_params = SamplingParams(temperature=0, top_p=0.95)

# Create an LLM.
llm = LLM(model=quant_path, quantization="AWQ")
# Generate texts from the prompts. The output is a list of RequestOutput objects
# that contain the prompt, generated text, and other information.


ModuleNotFoundError: No module named 'vllm'

In [ ]:
# Sample prompts.
prompts = [
    "Hello, my name is",
    "The president of the United States is",
    "The capital of France is",
    "The future of AI is",
]


outputs = llm.generate(prompts, sampling_params)
# Print the outputs.
for output in outputs:
    prompt = output.prompt
    generated_text = output.outputs[0].text
    print(f"Prompt: {prompt!r}, Generated text: {generated_text!r}")